In [1]:
import os
import numpy as np 
import pandas as pd
from pathlib import Path
import glob
import pickle as pkl
import matplotlib.pyplot as plt
import random
import scipy
import torch
import io
from scipy import signal

/home/boehlke/programs/anaconda3/envs/ava-test4/lib/python3.8/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


## All Metrics For All Experiments Dictionary
 The results dict created with many ufly loops and conditions in this notebook should contain all results for all experiments conducted. 
 It is structured as follows \[memory filling strategy\]\[shuffled_or_not\]\[dataratio\]\[epoch\]\[rehearsal method\]
 
I suggest just looking at the subdictionaries' keys() to see the possible options

Below there is a function, that when called prints latex tabular statements to kickstart the generation of a latex table. It probably needs to be fomrated still. 

In [ ]:
# for example
results_dict['inf']['shuffled_']['8.0']['5']['cf']

In [7]:
res_root = '/home/boehlke_data/'

In [65]:
data_ratios = ['2.0','8.0']
epochs = ['5', '3'] # ,'6', '9','15','27','40']

cv_splits = ['0', '1', '2', '3', '4']
shuffled = ['', 'shuffled_']
strategies = ['naive', 'joint', 'ce', 'cf', 'rr', 'mir', 'wce', 'feo','fe', 'cefa', 'ce_temp']
memory_filling_strategies = ['inf', 'stdrs', 'cbrs']
mem_sizes = ['0.1', '0.25']
temperatures = ['0.1','0.2','0.3']
sigmas = ['1.5', '3.0', '6.0','9.0']
wce_n_history = ['6','12','18']
metrics =['ClassTop_1AvgAcc_Stream',' ClassTop_2AvgAcc_Stream',
          'SummerClassTop_1AvgAcc_Stream','WinterClassTop_1AvgAcc_Stream',
          'Top_1Acc_Stream','SummerTop_1Acc_Stream','WinterTop_1Acc_Stream',
          'SeqTop_1Acc_Stream','SeqMAXAcc_Stream','SummerSeqTop_1Acc_Stream',
          'WinterSeqTop_1Acc_Stream','SeqClassTop_1AvgAcc_Stream',
          'SeqClassAvgMAXAcc_Stream','SummerSeqClassTop_1Acc_Stream',
          'WinterSeqClassTop_1Acc_Stream','SeqAnyAcc_Stream',
          'Cls0','Cls1','Cls2','Cls3','Cls4','Cls5','Cls6','Cls7','Cls8','Cls9',
          'Cls10','SeqCls0','SeqCls1','SeqCls2','SeqCls3','SeqCls4','SeqCls5',
          'SeqCls6','SeqCls7','SeqCls8','SeqCls9','SeqCls10']


#strategy = 'rehersal_ce_dataratio'+dr+'_ep'+ep+'_ne5/'
#cv_split = 'cv'+cv+'_expsize128_crop/'
len(metrics)

38

In [942]:
results_dict = {}
for memory in memory_filling_strategies: 
    results_dict[memory]={}
    for shuffl in shuffled: 
        results_dict[memory][shuffl] ={}
        for dr in data_ratios:
            results_dict[memory][shuffl][dr]={}
            for ep in epochs:
                results_dict[memory][shuffl][dr][ep] = {}
                for strat in strategies:
                    for cv in cv_splits:
                        cv_split = 'cv'+cv+'_expsize128_crop'
                        if memory == 'inf':
                            if strat == 'naive':
                                strategy_name =  'naive_'+shuffl+'ep'+str(ep)+'_ne'
                                metrics_dict = fill_results_dict(strategy_name, cv_split, results_dict)
                                if metrics_dict !=0:
                                    if strat in results_dict[memory][shuffl][dr][ep].keys():
                                        results_dict[memory][shuffl][dr][ep][strat] = join_metrics(metrics_dict, results_dict[memory][shuffl][dr][ep][strat])
                                    else:
                                        results_dict[memory][shuffl][dr][ep][strat] = metrics_dict
            
                
                            elif strat == 'joint':
                                strategy_name = 'joint_ep'+str(int((float(dr)+1)*int(ep)))+'_ne'
                                if int((float(dr)+1)*int(ep)) ==45:
                                        strategy_name = 'joint_ep40_ne'
                                metrics_dict = fill_results_dict(strategy_name, cv_split, results_dict)
                                if metrics_dict !=0:
                                    if strat in results_dict[memory][shuffl][dr][ep].keys():
                                        results_dict[memory][shuffl][dr][ep][strat] = join_metrics(metrics_dict, results_dict[memory][shuffl][dr][ep][strat])
                                    else:
                                        results_dict[memory][shuffl][dr][ep][strat] = metrics_dict
                            else:
                                if strat == 'ce_temp':
                                    for temp in temperatures:
                                        dict_identifier = 'ce_temp'+str(temp)
                                        strategy_name = 'rehersal_'+shuffl+'ce_temp'+str(temp)+'_dataratio'+dr+'_ep'+ep+'_ne'
                                        metrics_dict = fill_results_dict(strategy_name, cv_split, results_dict)
                                        if metrics_dict !=0:
                                            if dict_identifier in results_dict[memory][shuffl][dr][ep].keys():
                                                results_dict[memory][shuffl][dr][ep][dict_identifier] = join_metrics(metrics_dict, results_dict[memory][shuffl][dr][ep][dict_identifier])
                                            else:
                                                results_dict[memory][shuffl][dr][ep][dict_identifier] = metrics_dict
                                elif strat == 'wce':
                                    for navg in wce_n_history:
                                        for sigma in sigmas:
                                            dict_identifier = 'wce_navg'+navg+'_sigma'+sigma
                                            strategy_name = 'rehersal_'+shuffl+'wce_navg'+navg+'_sigma'+sigma+'_dataratio'+dr+'_ep'+ep+'_ne'
                                            metrics_dict = fill_results_dict(strategy_name, cv_split, results_dict)
                                            if metrics_dict !=0:
                                                if dict_identifier in results_dict[memory][shuffl][dr][ep].keys():
                                                    results_dict[memory][shuffl][dr][ep][dict_identifier] = join_metrics(metrics_dict, results_dict[memory][shuffl][dr][ep][dict_identifier])
                                                else:
                                                    results_dict[memory][shuffl][dr][ep][dict_identifier] = metrics_dict
                                               
                                else:
                                    strategy_name = 'rehersal_'+shuffl+strat+'_dataratio'+dr+'_ep'+ep+'_ne'
                                    metrics_dict = fill_results_dict(strategy_name, cv_split, results_dict)
                                    if metrics_dict !=0:
                                        if strat in results_dict[memory][shuffl][dr][ep].keys():
                                            results_dict[memory][shuffl][dr][ep][strat] = join_metrics(metrics_dict, results_dict[memory][shuffl][dr][ep][strat])
                                        else:
                                            results_dict[memory][shuffl][dr][ep][strat] = metrics_dict
                        else:
                            if strat in ['ce', 'cf','rr']:
                                for mem_size in mem_sizes:
                                    dict_identifier = memory+'_memsize'+mem_size+'_'+strat
                                    strategy_name = 'rehersal_'+memory+'_memsize_'+mem_size+'_'+shuffl+strat+'_dataratio'+dr+'_ep'+ep+'_ne'
                                    metrics_dict = fill_results_dict(strategy_name, cv_split, results_dict)
                                    
                                    if metrics_dict !=0:
                                        if dict_identifier in results_dict[memory][shuffl][dr][ep].keys():
                                            results_dict[memory][shuffl][dr][ep][dict_identifier] = join_metrics(metrics_dict, results_dict[memory][shuffl][dr][ep][dict_identifier])
                                        else:
                                            results_dict[memory][shuffl][dr][ep][dict_identifier] = metrics_dict


['/home/boehlke_data/rr_ce_cf_mir_results/resnet18_smoothloss_adamW_eps0.0001wd0.075_bs128/cv0_expsize128_crop/naive_ep5_ne5/']
['/home/boehlke_data/rr_ce_cf_mir_results/resnet18_smoothloss_adamW_eps0.0001wd0.075_bs128/cv0_expsize128_crop/naive_ep5_ne5/gen_csvlogs_2022-05-17_16-09-23-60/_test_stream.csv']
dict_keys(['train_exp', 'epoch', 'train exp classes', 'ClassTop_1AvgAcc_Stream', 'ClassTop_2AvgAcc_Stream', 'SummerClassTop_1AvgAcc_Stream', 'WinterClassTop_1AvgAcc_Stream', 'Top_1Acc_Stream', 'SummerTop_1Acc_Stream', 'WinterTop_1Acc_Stream', 'SeqTop_1Acc_Stream', 'SummerSeqTop_1Acc_Stream', 'WinterSeqTop_1Acc_Stream', 'SeqClassTop_1AvgAcc_Stream', 'SummerSeqClassTop_1Acc_Stream', 'WinterSeqClassTop_1Acc_Stream', 'SeqAnyAcc_Stream', 'Cls0', 'Cls1', 'Cls2', 'Cls3', 'Cls4', 'Cls5', 'Cls6', 'Cls7', 'Cls8', 'Cls9', 'Cls10', 'SeqCls0', 'SeqCls1', 'SeqCls2', 'SeqCls3', 'SeqCls4', 'SeqCls5', 'SeqCls6', 'SeqCls7', 'SeqCls8', 'SeqCls9', 'SeqCls10'])
['/home/boehlke_data/rr_ce_cf_mir_results/re

dict_keys(['train_exp', 'epoch', 'train exp classes', 'ClassTop_1AvgAcc_Stream', 'ClassTop_2AvgAcc_Stream', 'SummerClassTop_1AvgAcc_Stream', 'WinterClassTop_1AvgAcc_Stream', 'Top_1Acc_Stream', 'SummerTop_1Acc_Stream', 'WinterTop_1Acc_Stream', 'SeqTop_1Acc_Stream', 'SummerSeqTop_1Acc_Stream', 'WinterSeqTop_1Acc_Stream', 'SeqClassTop_1AvgAcc_Stream', 'SummerSeqClassTop_1Acc_Stream', 'WinterSeqClassTop_1Acc_Stream', 'SeqAnyAcc_Stream', 'Cls0', 'Cls1', 'Cls2', 'Cls3', 'Cls4', 'Cls5', 'Cls6', 'Cls7', 'Cls8', 'Cls9', 'Cls10', 'SeqCls0', 'SeqCls1', 'SeqCls2', 'SeqCls3', 'SeqCls4', 'SeqCls5', 'SeqCls6', 'SeqCls7', 'SeqCls8', 'SeqCls9', 'SeqCls10'])
['/home/boehlke_data/rr_ce_cf_mir_results/resnet18_smoothloss_adamW_eps0.0001wd0.075_bs128/cv3_expsize128_crop/rehersal_cf_dataratio2.0_ep3_ne10/']
['/home/boehlke_data/rr_ce_cf_mir_results/resnet18_smoothloss_adamW_eps0.0001wd0.075_bs128/cv3_expsize128_crop/rehersal_cf_dataratio2.0_ep3_ne10/gen_csvlogs_2022-05-13_23-07-31-06/_test_stream.csv']
dict

['/home/boehlke_data/rr_ce_cf_mir_results/resnet18_smoothloss_adamW_eps0.0001wd0.075_bs128/cv2_expsize128_crop/naive_ep3_ne5/gen_csvlogs_2022-05-15_08-09-41-16/_test_stream.csv']
dict_keys(['train_exp', 'epoch', 'train exp classes', 'ClassTop_1AvgAcc_Stream', 'ClassTop_2AvgAcc_Stream', 'SummerClassTop_1AvgAcc_Stream', 'WinterClassTop_1AvgAcc_Stream', 'Top_1Acc_Stream', 'SummerTop_1Acc_Stream', 'WinterTop_1Acc_Stream', 'SeqTop_1Acc_Stream', 'SummerSeqTop_1Acc_Stream', 'WinterSeqTop_1Acc_Stream', 'SeqClassTop_1AvgAcc_Stream', 'SummerSeqClassTop_1Acc_Stream', 'WinterSeqClassTop_1Acc_Stream', 'SeqAnyAcc_Stream', 'Cls0', 'Cls1', 'Cls2', 'Cls3', 'Cls4', 'Cls5', 'Cls6', 'Cls7', 'Cls8', 'Cls9', 'Cls10', 'SeqCls0', 'SeqCls1', 'SeqCls2', 'SeqCls3', 'SeqCls4', 'SeqCls5', 'SeqCls6', 'SeqCls7', 'SeqCls8', 'SeqCls9', 'SeqCls10'])
['/home/boehlke_data/rr_ce_cf_mir_results/resnet18_smoothloss_adamW_eps0.0001wd0.075_bs128/cv3_expsize128_crop/naive_ep3_ne5/']
['/home/boehlke_data/rr_ce_cf_mir_results/re

dict_keys(['train_exp', 'epoch', 'train exp classes', 'ClassTop_1AvgAcc_Stream', 'ClassTop_2AvgAcc_Stream', 'SummerClassTop_1AvgAcc_Stream', 'WinterClassTop_1AvgAcc_Stream', 'Top_1Acc_Stream', 'SummerTop_1Acc_Stream', 'WinterTop_1Acc_Stream', 'SeqTop_1Acc_Stream', 'SeqMAXAcc_Stream', 'SummerSeqTop_1Acc_Stream', 'WinterSeqTop_1Acc_Stream', 'SeqClassTop_1AvgAcc_Stream', 'SeqClassAvgMAXAcc_Stream', 'SummerSeqClassTop_1Acc_Stream', 'WinterSeqClassTop_1Acc_Stream', 'SeqAnyAcc_Stream', 'Cls0', 'Cls1', 'Cls2', 'Cls3', 'Cls4', 'Cls5', 'Cls6', 'Cls7', 'Cls8', 'Cls9', 'Cls10', 'SeqCls0', 'SeqCls1', 'SeqCls2', 'SeqCls3', 'SeqCls4', 'SeqCls5', 'SeqCls6', 'SeqCls7', 'SeqCls8', 'SeqCls9', 'SeqCls10'])
['/home/boehlke_data/ce_temp_results/resnet18_smoothloss_adamW_eps0.0001wd0.075_bs128/cv4_expsize128_crop/rehersal_ce_temp0.1_dataratio8.0_ep3_ne5/']
['/home/boehlke_data/ce_temp_results/resnet18_smoothloss_adamW_eps0.0001wd0.075_bs128/cv4_expsize128_crop/rehersal_ce_temp0.1_dataratio8.0_ep3_ne5/gen_cs

['/home/boehlke_data/rr_ce_cf_mir_results/resnet18_smoothloss_adamW_eps0.0001wd0.075_bs128/cv3_expsize128_crop/naive_shuffled_ep5_ne100/']
['/home/boehlke_data/rr_ce_cf_mir_results/resnet18_smoothloss_adamW_eps0.0001wd0.075_bs128/cv3_expsize128_crop/naive_shuffled_ep5_ne100/gen_csvlogs_2022-05-20_01-10-05-31/_test_stream.csv']
dict_keys(['train_exp', 'epoch', 'train exp classes', 'ClassTop_1AvgAcc_Stream', 'ClassTop_2AvgAcc_Stream', 'SummerClassTop_1AvgAcc_Stream', 'WinterClassTop_1AvgAcc_Stream', 'Top_1Acc_Stream', 'SummerTop_1Acc_Stream', 'WinterTop_1Acc_Stream', 'SeqTop_1Acc_Stream', 'SummerSeqTop_1Acc_Stream', 'WinterSeqTop_1Acc_Stream', 'SeqClassTop_1AvgAcc_Stream', 'SummerSeqClassTop_1Acc_Stream', 'WinterSeqClassTop_1Acc_Stream', 'SeqAnyAcc_Stream', 'Cls0', 'Cls1', 'Cls2', 'Cls3', 'Cls4', 'Cls5', 'Cls6', 'Cls7', 'Cls8', 'Cls9', 'Cls10', 'SeqCls0', 'SeqCls1', 'SeqCls2', 'SeqCls3', 'SeqCls4', 'SeqCls5', 'SeqCls6', 'SeqCls7', 'SeqCls8', 'SeqCls9', 'SeqCls10'])
['/home/boehlke_data/r

['/home/boehlke_data/rr_ce_cf_mir_results/resnet18_smoothloss_adamW_eps0.0001wd0.075_bs128/cv0_expsize128_crop/rehersal_shuffled_ce_dataratio8.0_ep3_ne5/']
['/home/boehlke_data/rr_ce_cf_mir_results/resnet18_smoothloss_adamW_eps0.0001wd0.075_bs128/cv0_expsize128_crop/rehersal_shuffled_ce_dataratio8.0_ep3_ne5/gen_csvlogs_2022-05-14_00-41-08-46/_test_stream.csv']
dict_keys(['train_exp', 'epoch', 'train exp classes', 'ClassTop_1AvgAcc_Stream', 'ClassTop_2AvgAcc_Stream', 'SummerClassTop_1AvgAcc_Stream', 'WinterClassTop_1AvgAcc_Stream', 'Top_1Acc_Stream', 'SummerTop_1Acc_Stream', 'WinterTop_1Acc_Stream', 'SeqTop_1Acc_Stream', 'SummerSeqTop_1Acc_Stream', 'WinterSeqTop_1Acc_Stream', 'SeqClassTop_1AvgAcc_Stream', 'SummerSeqClassTop_1Acc_Stream', 'WinterSeqClassTop_1Acc_Stream', 'SeqAnyAcc_Stream', 'Cls0', 'Cls1', 'Cls2', 'Cls3', 'Cls4', 'Cls5', 'Cls6', 'Cls7', 'Cls8', 'Cls9', 'Cls10', 'SeqCls0', 'SeqCls1', 'SeqCls2', 'SeqCls3', 'SeqCls4', 'SeqCls5', 'SeqCls6', 'SeqCls7', 'SeqCls8', 'SeqCls9', '

[]
[]
[]
['/home/boehlke_data/wce_results/resnet18_smoothloss_adamW_eps0.0001wd0.075_bs128/cv4_expsize128_crop/rehersal_shuffled_wce_navg12_sigma3.0_dataratio8.0_ep3_ne5/']
['/home/boehlke_data/wce_results/resnet18_smoothloss_adamW_eps0.0001wd0.075_bs128/cv4_expsize128_crop/rehersal_shuffled_wce_navg12_sigma3.0_dataratio8.0_ep3_ne5/gen_csvlogs_2022-07-09_00-46-12-67/_test_stream.csv']
dict_keys(['train_exp', 'epoch', 'train exp classes', 'ClassTop_1AvgAcc_Stream', 'ClassTop_2AvgAcc_Stream', 'SummerClassTop_1AvgAcc_Stream', 'WinterClassTop_1AvgAcc_Stream', 'Top_1Acc_Stream', 'SummerTop_1Acc_Stream', 'WinterTop_1Acc_Stream', 'SeqTop_1Acc_Stream', 'SeqMAXAcc_Stream', 'SummerSeqTop_1Acc_Stream', 'WinterSeqTop_1Acc_Stream', 'SeqClassTop_1AvgAcc_Stream', 'SeqClassAvgMAXAcc_Stream', 'SummerSeqClassTop_1Acc_Stream', 'WinterSeqClassTop_1Acc_Stream', 'SeqAnyAcc_Stream', 'Cls0', 'Cls1', 'Cls2', 'Cls3', 'Cls4', 'Cls5', 'Cls6', 'Cls7', 'Cls8', 'Cls9', 'Cls10', 'SeqCls0', 'SeqCls1', 'SeqCls2', 'SeqC

['/home/boehlke_data/stdrs_results/resnet18_smoothloss_adamW_eps0.0001wd0.075_bs128/cv3_expsize128_crop/rehersal_stdrs_memsize_0.1_rr_dataratio8.0_ep5_ne100/']
['/home/boehlke_data/stdrs_results/resnet18_smoothloss_adamW_eps0.0001wd0.075_bs128/cv3_expsize128_crop/rehersal_stdrs_memsize_0.1_rr_dataratio8.0_ep5_ne100/gen_csvlogs_2022-08-05_18-54-45-10/_test_stream.csv']
dict_keys(['train_exp', 'epoch', 'train exp classes', 'ClassTop_1AvgAcc_Stream', 'ClassTop_2AvgAcc_Stream', 'SummerClassTop_1AvgAcc_Stream', 'WinterClassTop_1AvgAcc_Stream', 'Top_1Acc_Stream', 'SummerTop_1Acc_Stream', 'WinterTop_1Acc_Stream', 'SeqTop_1Acc_Stream', 'SeqMAXAcc_Stream', 'SummerSeqTop_1Acc_Stream', 'WinterSeqTop_1Acc_Stream', 'SeqClassTop_1AvgAcc_Stream', 'SeqClassAvgMAXAcc_Stream', 'SummerSeqClassTop_1Acc_Stream', 'WinterSeqClassTop_1Acc_Stream', 'SeqAnyAcc_Stream', 'Cls0', 'Cls1', 'Cls2', 'Cls3', 'Cls4', 'Cls5', 'Cls6', 'Cls7', 'Cls8', 'Cls9', 'Cls10', 'SeqCls0', 'SeqCls1', 'SeqCls2', 'SeqCls3', 'SeqCls4', 

dict_keys(['train_exp', 'epoch', 'train exp classes', 'ClassTop_1AvgAcc_Stream', 'ClassTop_2AvgAcc_Stream', 'SummerClassTop_1AvgAcc_Stream', 'WinterClassTop_1AvgAcc_Stream', 'Top_1Acc_Stream', 'SummerTop_1Acc_Stream', 'WinterTop_1Acc_Stream', 'SeqTop_1Acc_Stream', 'SeqMAXAcc_Stream', 'SummerSeqTop_1Acc_Stream', 'WinterSeqTop_1Acc_Stream', 'SeqClassTop_1AvgAcc_Stream', 'SeqClassAvgMAXAcc_Stream', 'SummerSeqClassTop_1Acc_Stream', 'WinterSeqClassTop_1Acc_Stream', 'SeqAnyAcc_Stream', 'Cls0', 'Cls1', 'Cls2', 'Cls3', 'Cls4', 'Cls5', 'Cls6', 'Cls7', 'Cls8', 'Cls9', 'Cls10', 'SeqCls0', 'SeqCls1', 'SeqCls2', 'SeqCls3', 'SeqCls4', 'SeqCls5', 'SeqCls6', 'SeqCls7', 'SeqCls8', 'SeqCls9', 'SeqCls10'])
rehersal_cbrs_memsize_0.25_ce_dataratio8.0_ep5_ne
['/home/boehlke_data/cbrs_results_new/resnet18_smoothloss_adamW_eps0.0001wd0.075_bs128/cv3_expsize128_crop/rehersal_cbrs_memsize_0.25_ce_dataratio8.0_ep5_ne5/']
['/home/boehlke_data/cbrs_results_new/resnet18_smoothloss_adamW_eps0.0001wd0.075_bs128/cv3_e

In [892]:
def join_metrics(metrics_dict, results_dict):
    for key, value in metrics_dict.items():
        if key in results_dict.keys():
            results_dict[key].append(value[0])
    return results_dict

In [943]:
def fill_results_dict(strategy_name,cv_split,  results_dict, data_type='test'):
    metrics_dict = {}
    strategy_results_path = glob.glob(res_root+'/*/'+'resnet18_smoothloss_adamW_eps0.0001wd0.075_bs128/'+cv_split+'/'+strategy_name+'*/')
    if len(strategy_results_path)< 1:
        return 0
    path = strategy_results_path[0]+'*exp*_'+data_type+'_confusion_data_dict.pkl'
    res_pkl_path = glob.glob(strategy_results_path[0]+'*exp*_'+data_type+'_confusion_data_dict.pkl')
    res_csv =  glob.glob(strategy_results_path[0]+'/gen_csvlogs*/_'+data_type+'_stream.csv')
    if len(res_pkl_path)>1:
        exp_eval_list =[]
        for i in res_pkl_path:
            exp_eval = int(i.split('_after_exp')[-1].split('_')[0])
            exp_eval_list.append(exp_eval)
        last_eval_exp = np.argmax(np.array(exp_eval_list))
        res_pkl = [res_pkl_path[last_eval_exp]]
        #print('res_csv ', res_csv)
        if len(res_csv) >=1:
            res_csv_data =  pd.read_csv(res_csv[-1], low_memory=False)
            #print(res_csv_data.iloc[-1,0])
            #print( exp_eval_list[last_eval_exp])
            if res_csv_data.iloc[-1,0] == exp_eval_list[last_eval_exp]:
                #relevant_row = res_csv_data.iloc[-1,:]
                #print(relevant_row.columns)
                for col in res_csv_data.columns:
                        metrics_dict[col] = [res_csv_data[col].iloc[-1]]
                print(metrics_dict.keys())
                return metrics_dict 
            else: 
                print('NOT TREAIN EXO')
                print(res_csv_data.iloc[-1,0])
                print(exp_eval_list[last_eval_exp])
           
        
    else: 
        print(res_pkl_path)
        print(path)
        print('res_pkl not found? ')
        print(cv_split+'/'+strategy_name)
        return 0
    
    
    

In [941]:
def create_res_table(res_dict, memory, shuffled, dataratios, epochs, strategies, metrics):
    total_col = len(strategies)*len(epochs)*len(dataratios)
    two_rows_per_metric = False
    if len(epochs) >1:
        two_rows_per_metric = True

    res_array = np.zeros((len(metrics), 1)) 
    std_array =  np.zeros((len(metrics), 1))
    title_list = []

    for i, epoch in enumerate(epochs):
        if i ==1: # two number for epochs will be merged together later, does not handle more than two epoch settings...
            epoch0_res_array  = res_array[:,1:]
            epoch0_std_array = std_array[:,1:]
            res_array = np.empty((len(metrics), 1)) 
            std_array =  np.empty((len(metrics), 1))
        for s, strat in enumerate(strategies):
            if 'cbrs' in strat:
                memory = 'cbrs'
            elif 'stdrs' in strat:
                memory = 'stdrs'
            for shuffl in shuffled:
                for dr in dataratios:
                    title_list.append(strat+'_'+shuffl+'dr'+dr)
                    res_col = np.empty((len(metrics),1))
                    std_col = np.empty((len(metrics), 1))
                    if strat in results_dict[memory][shuffl][dr][epoch].keys():
                        metrics_dict = results_dict[memory][shuffl][dr][epoch][strat]
                        for j, metric in enumerate(metrics):
                            if metric in results_dict[memory][shuffl][dr][epoch][strat].keys():
                                if len(metrics_dict[metric])<4:
                                    print(metrics_dict[metric])
                                    print(metric, strat, dr, ep, shuffl)
                                metric_res_list = np.array(metrics_dict[metric])
                                metric_avg = np.round(np.mean(metric_res_list), 4)
                                metric_std = np.round(np.std(metric_res_list), 4)
                                res_col[j] = np.round(metric_avg*100, 2)
                                std_col[j] = np.round(metric_std*100, 2)
                    else:
                        res_col = np.array(['-']*len(metrics)).reshape((len(metrics),1))
                        std_col = np.array(['-']*len(metrics)).reshape((len(metrics),1))
                    res_array = np.concatenate([res_array, res_col], axis=1)
                    std_array = np.concatenate([std_array, std_col], axis=1)

    epoch1_res_array = res_array[:,1:]
    epoch1_std_array = std_array[:,1:]
    col_title_list = metrics
    if len(epochs)>1:
        col_title_list = []
        full_res_array = np.zeros((1,epoch0_res_array.shape[1]))
        full_std_array = np.zeros((1,epoch0_res_array.shape[1]))
        print(full_res_array.shape)
        for i, metric in enumerate(metrics):
            col_title_list.append(metric+'_ep'+epochs[0])
            col_title_list.append(metric+'_ep'+epochs[1])
            full_res_array = np.concatenate([full_res_array, epoch0_res_array[[i],:]], axis=0)
            full_res_array = np.concatenate([full_res_array, epoch1_res_array[[i],:]], axis=0)
            full_std_array = np.concatenate([full_std_array, epoch0_std_array[[i],:]], axis=0)
            full_std_array = np.concatenate([full_std_array, epoch1_std_array[[i],:]], axis=0)
            
        full_std_array = full_std_array[1:,:]
        full_res_array = full_res_array[1:,:]
    else: 
        full_res_array = epoch1_res_array
        full_std_array = epoch1_std_array

    accs_n_stds = np.chararray(full_res_array.shape, itemsize=15)
    for i, j in np.ndindex(full_std_array.shape):
        
        if full_res_array[i,j] == '-':
            accs_n_stds[i,j] = '-'
        else:
            accs_n_stds[i,j] = '$'+str(full_res_array[i,j])+'\pm'+ str(full_std_array[i,j])+'$'
    epochs_col = np.array([epochs*len(metrics)]).T
    accs_n_stds = np.concatenate([epochs_col,accs_n_stds], axis=1)
    accs_n_stds = np.concatenate([np.array(col_title_list).reshape((len(col_title_list),1)), accs_n_stds], axis=1)
    if len(epochs)>1:
        title_list = title_list[:int(len(title_list)/2)]
    if '' in shuffled :
        order = 'chronological'
    else:
        order = 'shuffled'
    title_list = ['metric', 'epochs']+title_list
    multi_col = len(shuffled)*len(dataratios)
    latex_title = '\multicolumn{2}{c}{}'
    dataratio_title ='\multicolumn{2}{c}{dataratio}'
    shuffle_title = '\multicolumn{2}{c}{data stream order : }'
    shuffle_title2 = '\multicolumn{2}{c}{data stream: '+order+'}'
    metric_epoch_title = 'metric & epochs '
    for strat in strategies:
        if strat in strategies_dict.keys() :
            latex_title = latex_title +'&\multicolumn{'+str(multi_col)+'}{c}{'+strategies_dict[strat]+'}'
        elif strat[-2:] in strategies_dict.keys():
            if 'cbrs' in strat:
                mem_filling = 'CBRS '
            else: 
                mem_filling = 'STDRS '
            latex_title = latex_title +'&\multicolumn{'+str(multi_col)+'}{c}{'+mem_filling+strategies_dict[strat[-2:]]+'}'
            
        else:
            latex_title = latex_title +'&\multicolumn{'+str(multi_col)+'}{c}{'+strat.replace('_', '\\_')+'}'
        if len(shuffled)==2:
            for dr in dataratios:
                shuffle_title = shuffle_title+'&\multicolumn{'+str(int(multi_col/2))+'}{c}{chronological}'+'&\multicolumn{'+str(int(multi_col/2))+'}{c}{shuffled}'
        else:   
            for dr in dataratios:
                shuffle_title = shuffle_title+'&\multicolumn{'+str(int(multi_col/2))+'}{c}{'+order+'}'
        for i in range(len(shuffled)):
            for dr in dataratios:
                metric_epoch_title  = metric_epoch_title+'&'
                shuffle_title2 = shuffle_title2 + '&'
                dataratio_title = dataratio_title+ '&r='+dr
                

    dataratio_title = dataratio_title +'\\\\ [.1cm] \hline'
    latex_title = latex_title +'\\\\'
    shuffle_title = shuffle_title+ '\\\\'
    shuffle_title2 = shuffle_title2+ '\\\\'
    metric_epoch_title  = metric_epoch_title+'\\\\ [.2cm]'
    print(latex_title)
    print(shuffle_title)
    print(shuffle_title2)
    print(dataratio_title)
    print(metric_epoch_title)
    for i, row in enumerate(accs_n_stds):
        next_line = ''
        if np.unique(accs_n_stds[:,1]).shape[0]==2:
            for j, element in enumerate(row):
                if j == 0:
                    if i%2 ==0:
                        next_line = next_line+'\multirow{2}{*}{'+element.split('_ep')[0].replace('_', '\\_')+'}'
                    else:
                        next_line = next_line+''
                else: 
                     next_line = next_line+'&'+element
        else: 
            for j, element in enumerate(row):
                    if j == 0:
                        next_line = next_line+element.split('_ep')[0].replace('_', '\\_')  
                    else:
                        next_line = next_line+'&'+element
        next_line = next_line +'\\\\'
        if np.unique(accs_n_stds[:,1]).shape[0]==2:
            if i%2 ==1:
                 next_line = next_line +'[.3cm]'
        print(next_line)
    return accs_n_stds, title_list

In [849]:
global strategies_dict
strategies_dict = {'ce': 'Class Error',
                  'cf': 'Class Frequency',
                  'rr': 'Random',
                  'mir': 'Max. Interfered Retrival',
                  'feo': 'Fill Exp - Oversample',
                  'fe': 'Fill Exp - Random',
                  'cefa': 'Cls Error/Freq Avg',
                   'joint': 'Joint',
                   'naive': 'Naive'
                  }

In [873]:
results_dict['inf']['']['8.0']['3'].keys()

dict_keys(['naive', 'joint', 'ce', 'cf', 'rr', 'mir', 'wce_navg6_sigma3.0', 'wce_navg12_sigma3.0', 'wce_navg12_sigma6.0', 'wce_navg18_sigma9.0', 'feo', 'fe', 'cefa', 'ce_temp0.1', 'ce_temp0.2', 'ce_temp0.3'])

In [936]:
results_dict['cbrs']['']['8.0']['5']['cbrs_memsize0.25_ce']

{'train_exp': [260, 266, 266, 255],
 'epoch': [4, 4, 4, 4],
 'train exp classes': ['[1 3 4 7 10 ]', '[10 4 7 ]', '[10 4 7 ]', '[10 7 ]'],
 'ClassTop_1AvgAcc_Stream': [0.6787, 0.6866, 0.658, 0.6819],
 'ClassTop_2AvgAcc_Stream': [0.778, 0.7858, 0.7628, 0.7707],
 'SummerClassTop_1AvgAcc_Stream': [0.5036, 0.4878, 0.4727, 0.5552],
 'WinterClassTop_1AvgAcc_Stream': [0.7043, 0.6553, 0.6751, 0.7181],
 'Top_1Acc_Stream': [0.8311, 0.855, 0.8537, 0.8359],
 'SummerTop_1Acc_Stream': [0.8383, 0.8525, 0.8532, 0.8339],
 'WinterTop_1Acc_Stream': [0.8188, 0.8597, 0.8547, 0.8393],
 'SeqTop_1Acc_Stream': [0.847, 0.8681, 0.8512, 0.8398],
 'SeqMAXAcc_Stream': [0.841, 0.8608, 0.8434, 0.8018],
 'SummerSeqTop_1Acc_Stream': [0.8545, 0.8682, 0.8554, 0.8485],
 'WinterSeqTop_1Acc_Stream': [0.8354, 0.8678, 0.8443, 0.8265],
 'SeqClassTop_1AvgAcc_Stream': [0.6492, 0.7028, 0.6471, 0.6625],
 'SeqClassAvgMAXAcc_Stream': [0.661, 0.7049, 0.6707, 0.6619],
 'SummerSeqClassTop_1Acc_Stream': [0.4556, 0.5208, 0.5294, 0.5613],


In [915]:
results_dict['inf']['shuffled_']['8.0']['5']['cf']

{'train_exp': [260, 263, 266, 266],
 'epoch': [4, 4, 4, 4],
 'train exp classes': ['[0 3 4 6 7 9 10 ]',
  '[0 1 3 4 5 6 7 8 9 10 ]',
  '[0 3 4 6 7 9 10 ]',
  '[0 1 2 3 4 5 6 7 8 10 ]'],
 'ClassTop_1AvgAcc_Stream': [0.6983, 0.7101, 0.6874, 0.7089],
 'ClassTop_2AvgAcc_Stream': [0.79, 0.7878, 0.7909, 0.7717],
 'SummerClassTop_1AvgAcc_Stream': [0.5204, 0.6352, 0.5209, 0.5138],
 'WinterClassTop_1AvgAcc_Stream': [0.7548, 0.6653, 0.6623, 0.742],
 'Top_1Acc_Stream': [0.8696, 0.8806, 0.8661, 0.8573],
 'SummerTop_1Acc_Stream': [0.8681, 0.8757, 0.8673, 0.8523],
 'WinterTop_1Acc_Stream': [0.872, 0.8901, 0.8638, 0.8666],
 'SeqTop_1Acc_Stream': [0.8783, 0.8873, 0.8675, 0.8741],
 'SummerSeqTop_1Acc_Stream': [0.8723, 0.8953, 0.8672, 0.8679],
 'WinterSeqTop_1Acc_Stream': [0.8877, 0.8742, 0.8678, 0.8844],
 'SeqClassTop_1AvgAcc_Stream': [0.7114, 0.7204, 0.7106, 0.7003],
 'SummerSeqClassTop_1Acc_Stream': [0.5012, 0.6561, 0.5749, 0.5538],
 'WinterSeqClassTop_1Acc_Stream': [0.7999, 0.6823, 0.7028, 0.7405],


In [944]:
accs_n_stds, title_list = create_res_table(results_dict, 
                 memory = 'inf', 
                 shuffled = ['' ], 
                 dataratios= ['8.0'], 
                 epochs = ['3'], 
                 strategies = [ 'cf', 'ce', 'ce_temp0.1', 'ce_temp0.2', 'ce_temp0.3', 'wce_navg6_sigma1.5', 'wce_navg6_sigma3.0', 'wce_navg12_sigma3.0', 'wce_navg12_sigma6.0', 'wce_navg18_sigma9.0'], 
                 metrics = ['Top_1Acc_Stream','ClassTop_1AvgAcc_Stream', 'SeqTop_1Acc_Stream', 'SeqClassTop_1AvgAcc_Stream' ])
#print(title_list)
#print(len(title_list))
#print(accs_n_stds.shape)
#print(accs_n_stds)

accs_n_stds = pd.DataFrame(accs_n_stds)
accs_n_stds.to_csv('inf_chronological.csv', header=title_list)



\multicolumn{2}{c}{}&\multicolumn{1}{c}{Class Frequency}&\multicolumn{1}{c}{Class Error}&\multicolumn{1}{c}{ce\_temp0.1}&\multicolumn{1}{c}{ce\_temp0.2}&\multicolumn{1}{c}{ce\_temp0.3}&\multicolumn{1}{c}{wce\_navg6\_sigma1.5}&\multicolumn{1}{c}{wce\_navg6\_sigma3.0}&\multicolumn{1}{c}{wce\_navg12\_sigma3.0}&\multicolumn{1}{c}{wce\_navg12\_sigma6.0}&\multicolumn{1}{c}{wce\_navg18\_sigma9.0}\\
\multicolumn{2}{c}{data stream order : }&\multicolumn{0}{c}{chronological}&\multicolumn{0}{c}{chronological}&\multicolumn{0}{c}{chronological}&\multicolumn{0}{c}{chronological}&\multicolumn{0}{c}{chronological}&\multicolumn{0}{c}{chronological}&\multicolumn{0}{c}{chronological}&\multicolumn{0}{c}{chronological}&\multicolumn{0}{c}{chronological}&\multicolumn{0}{c}{chronological}\\
\multicolumn{2}{c}{data stream: chronological}&&&&&&&&&&\\
\multicolumn{2}{c}{dataratio}&r=8.0&r=8.0&r=8.0&r=8.0&r=8.0&r=8.0&r=8.0&r=8.0&r=8.0&r=8.0\\ [.1cm] \hline
metric & epochs &&&&&&&&&&\\ [.2cm]
Top\_1Acc\_Stream&3&$

In [939]:
accs_n_stds, title_list = create_res_table(results_dict, 
                 memory = 'stdrs', 
                 shuffled = ['', 'shuffled_' ], 
                 dataratios= ['8.0'], 
                 epochs = ['5'], 
                 strategies = [ 'cbrs_memsize0.1_ce', 'cbrs_memsize0.1_cf',  'cbrs_memsize0.1_rr','stdrs_memsize0.1_ce', 'stdrs_memsize0.1_cf',  'stdrs_memsize0.1_rr'], 
                 metrics = ['Top_1Acc_Stream','ClassTop_1AvgAcc_Stream', 'SeqTop_1Acc_Stream', 'SeqClassTop_1AvgAcc_Stream' ])

accs_n_stds = pd.DataFrame(accs_n_stds)
accs_n_stds.to_csv('accs_n_std.csv', header=title_list)


['', 'shuffled_']
2
strat:  cbrs_memsize0.1_ce
strat:  cbrs_memsize0.1_cf
strat:  cbrs_memsize0.1_rr
strat:  stdrs_memsize0.1_ce
strat:  stdrs_memsize0.1_cf
strat:  stdrs_memsize0.1_rr
epoch1_std_array
[[0.81 0.48 1.5  0.24 1.55 0.49 0.88 0.19 0.97 0.77 0.52 0.26]
 [0.99 1.41 2.52 0.68 1.67 1.31 1.72 2.52 1.66 2.36 1.43 2.58]
 [0.95 0.78 2.06 0.39 1.59 0.85 0.68 0.94 1.32 0.58 1.61 0.4 ]
 [1.41 3.24 3.68 1.34 3.23 1.18 2.35 3.76 2.89 2.28 2.91 2.42]]
(4, 12)
(4, 12)
[[b'$81.41\\pm0.81$' b'$88.31\\pm0.48$' b'$82.08\\pm1.5$'
  b'$88.33\\pm0.24$' b'$82.78\\pm1.55$' b'$88.38\\pm0.49$'
  b'$84.3\\pm0.88$' b'$88.22\\pm0.19$' b'$82.4\\pm0.97$'
  b'$88.38\\pm0.77$' b'$84.79\\pm0.52$' b'$89.11\\pm0.26$']
 [b'$65.38\\pm0.99$' b'$69.39\\pm1.41$' b'$66.43\\pm2.52$'
  b'$67.11\\pm0.68$' b'$66.39\\pm1.67$' b'$67.01\\pm1.31$'
  b'$50.3\\pm1.72$' b'$57.65\\pm2.52$' b'$49.34\\pm1.66$'
  b'$56.86\\pm2.36$' b'$48.71\\pm1.43$' b'$55.19\\pm2.58$']
 [b'$82.82\\pm0.95$' b'$89.42\\pm0.78$' b'$83.96\\pm2.06$'
